In [2]:
!mpremote cp ../../micropython-stubber/src/stubber/board/logging.py :logging.py
!mpremote cp ../../micropython-stubber/src/stubber/board/createstubs_info.py :createstubs.py

cp ../../micropython-stubber/src/stubber/board/logging.py :logging.py
cp ../../micropython-stubber/src/stubber/board/createstubs_info.py :createstubs.py


In [3]:
%mpy --select auto
!mpremote ls

ls :
       30017 createstubs.py
        2218 logging.py


In [4]:
%mpy import createstubs

['INFO  :stubber :Port: rp2', 'INFO  :stubber :Board: Pimoroni_Pico_LiPo_16MB_with_RP2040', 'INFO  :stubber :Clean/remove files in folder: /stubs/micropython-v1_19_1-rp2-Pimoroni_Pico_LiPo_16MB_with_RP2040', 'INFO  :stubber :Start micropython-stubber vv1.13.7 on micropython-v1.19.1-rp2-Pimoroni_Pico_LiPo_16MB_with_RP2040', 'WARN  :stubber :Skip module: WM8960                    Module not found.                                                              ', 'WARN  :stubber :Skip module: _OTA                      Module not found.                                                              ', '', '*** Memory info _boot_fat ***', 'stack: 1956 out of 7936', 'GC: total: 192064, used: 28560, free: 163504', ' No. of 1-blocks: 315, 2-blocks: 79, max blk sz: 79, max free sz: 7888', 'GC memory layout; from 20009520:', '00000000: MDMhhhhDhhSBMBDSDBhDh===BSB=Dh====B=BBBBBBBB=BBB=BBBBB=B=h===h==', '00000400: h=B=h===========h===================h=====h=================h===', '00000800: ==========

In [5]:
output = _

In [17]:
log_text = list(output.data)

In [39]:
from typing import List, Optional, Union
from colorama import Fore, Back, Style
import re
from dataclasses import dataclass, field
import copy


@dataclass
class MemoryInfo:
    """MicroPython Visual Memory Information Map"""

    # total: int = 0
    # """Total memory"""
    # used: int = 0
    # """Used memory"""
    # free: int = 0
    # """Free memory"""
    # one_blocks: int = 0
    # """Number of 1-blocks"""
    # two_blocks: int = 0
    # """Number of 2-blocks"""
    # max_block_size: int = 0
    # """Largest available block"""
    # max_free_size: int = 0
    # """largest free block"""
    memory_maps: List["MemoryInfo.Info"] = field(default_factory=list)
    # memory_map: str = ""
    """Memory map showing allocated and free areas"""
    # memory_map_2: str = ""
    # _raw_maps: List[List[str]] = field(default_factory=list)
    # _raw_map: str = ""
    # _raw_map_2: str = ""
    # lines_free: int = 0
    show_free: bool = True
    columns: int = 2
    rainbow: bool = False
    is_diff = False

    COL_WIDTH = 64

    @dataclass
    class Info:
        name: str = ""
        total: int = 0
        """Total memory"""
        used: int = 0
        """Used memory"""
        free: int = 0
        """Free memory"""
        one_blocks: int = 0
        """Number of 1-blocks"""
        two_blocks: int = 0
        """Number of 2-blocks"""
        max_block_size: int = 0
        """Largest available block"""
        max_free_size: int = 0
        """largest free block"""
        lines_free: int = 0
        map: str = ""
        _raw_map: str = ""

    def __init__(
        self,
        mem_info: Optional[Union[str, List[str]]] = "",
        name: Optional[str] = "",
        show_free: bool = False,
        columns: int = 4,
        rainbow: bool = False,
    ):
        """Parse the memory map"""
        self._raw_maps = []
        self.memory_maps = []
        columns = max(1, columns)
        rainbow = rainbow
        show_free = show_free
        self._color_num = 0
        if mem_info:
            self.append(mem_info, name)

    def append(
        self,
        mem_info: Union[str, List[str]],
        name: Optional[str] = "",
    ):
        """Append a new memory map"""
        # sourcery skip: use-named-expression
        if issubclass(type(mem_info), list):
            mem_info = "\n".join(mem_info)
        elif issubclass(type(mem_info), str):
            mem_info = str(mem_info)

        info = self.Info(name=name )

        match_1 = re.search(r"GC: total: (\d+), used: (\d+), free: (\d+)", mem_info)
        if not match_1:
            raise ValueError("Not recognized as a valid Micropython memory info")
        info.total, info.used, info.free = [int(x) for x in match_1.groups()]
        # find the used blocks
        match_2 = re.search(r" No. of 1-blocks: (\d+), 2-blocks: (\d+), max blk sz: (\d+), max free sz: (\d+)", mem_info)
        if match_2:
            info.one_blocks, info.two_blocks, info.max_block_size, info.max_free_size = [int(x) for x in match_2.groups()]
        match_3 = re.search(r"\((.*) lines all free\)", mem_info)
        if match_3:
            info.lines_free = int(match_3.groups(0)[0])
        info._raw_map = re.findall(r"^[0-9a-fA-F]*\: (.*)", mem_info, flags=re.MULTILINE)
        info.map = "".join(info._raw_map)
        self.memory_maps.append(info)
        self.update_map(info)

        # self._raw_maps.append(_raw_map)
        # self.memory_maps.append("".join(_raw_map))

        # self._raw_map = re.findall(r"^[0-9a-fA-F]*\: (.*)", mem_info, flags=re.MULTILINE)
        # self.memory_map = "".join(self._raw_map)
        # self.update_map(0)

    def update_map(self, info: Info):
        "show/hide the free space in the memory map"
        _map = info._raw_map.copy()  # type: ignore
        # TODO: Where to insert the free lines - currently just use -1 ...
        if self.show_free:
            for _ in range(info.lines_free):
                _map.insert(-1, "." * 64)
        info.memory_map = "".join(_map)

    def _repr_pretty_(self, pp, cycle):
        self._color_num = 0
        if len(self.memory_maps):
            if self.is_diff:
                return self._repr_pretty_diff_(pp, cycle)
            else:
                return self._repr_pretty_memmap_(pp, cycle)

    @property
    def used(self):
        return self.memory_maps[-1].used

    @property
    def total(self):
        return self.memory_maps[-1].total

    @property
    def free(self):
        return self.memory_maps[-1].free

    @property
    def total(self):
        return self.memory_maps[-1].total

    @property
    def one_blocks(self):
        return self.memory_maps[-1].one_blocks

    @property
    def two_blocks(self):
        return self.memory_maps[-1].two_blocks

    def _repr_pretty_memmap_(self, pp, cycle):
        "print a colored version of the memory map"
        width = self.COL_WIDTH * self.columns
        FIRST = 0
        LAST = -1
        cur_map = self.memory_maps[LAST].map

        # TODO - Update the used / totals etc from the _raw map - not the last one
        text = (
            f"{Fore.WHITE}{Back.BLACK}{self.memory_maps[LAST].name} \n"
            f"{Fore.WHITE}{Back.BLACK}Memory Used: 0x{self.used:X} of Total: 0x{self.total:X}\n"
            f"Free: 0x{self.free:X} {self.free/self.total:.1%}\n"
        )

        color = Fore.WHITE

        for i in range(len(cur_map)):
            # '=' keeps the same color
            if cur_map[i] != "=":
                color = self.color(cur_map[i])
            text += color + cur_map[i]
            # columns
            if (i + 1) % self.COL_WIDTH == 0:
                text += f"{Style.RESET_ALL} "
            # rows
            if (i + 1) % width == 0:
                text += Style.RESET_ALL + "\n"
        # now pretty print the memory map
        pp.text(text)

    def _repr_pretty_diff_(self, pp, cycle):
        """print a colored version of a differential memory map
        the  maps list should contain the 2 memory maps to compare, just compare the first and last ones for now
        """
        print("pretty print diff")
        FIRST = 0
        LAST = -1
        cur_map = self.memory_maps[FIRST].map

        width = self.COL_WIDTH * self.columns
        text = (
            # f"{Fore.WHITE}{Back.BLACK}Memory Used: 0x{self.used:X} of Total: 0x{self.total:X}\n"
            f"Free: 0x{self.free:X} {self.free/self.total:.1%}\n"
        )

        color = Fore.WHITE
        # max_range = max(len(self.memory_maps[FIRST]), len(self.memory_maps[LAST]))
        for i in range(len(cur_map)):
            # '=' keeps the same color

            this = cur_map[i] if i < len(cur_map) else ""
            other = cur_map[i] if i < len(cur_map) else ""
            color = self.diff_color(this, other)
            text += color + cur_map[i]
            # columns
            if (i + 1) % self.COL_WIDTH == 0:
                text += f"{Style.RESET_ALL} "
            # rows
            if (i + 1) % width == 0:
                text += Style.RESET_ALL + "\n"
        pp.text(text)

    def color(self, c: str):
        # ====== =================
        # Symbol Meaning
        # ====== =================
        #    .   free block
        #    h   head block
        #    =   tail block
        #    m   marked head block
        #    T   tuple
        #    L   list
        #    D   dict
        #    F   float
        #    B   byte code
        #    M   module
        #    S   string or bytes
        #    A   bytearray
        # ====== =================
        BG_COLORS = [Back.BLUE, Back.RED, Back.MAGENTA, Back.CYAN]
        fg = Fore.BLACK
        bg = Back.RED
        if c == ".":
            fg = Fore.GREEN
            bg = Back.GREEN
        elif c.isupper():
            fg = Fore.WHITE
        else:
            fg = Fore.BLACK
        if c in "TSLDFABh":
            if self.rainbow:
                bg = BG_COLORS[self._color_num]
                self._color_num = (self._color_num + 1) % len(BG_COLORS)
            else:
                bg = Back.RED
        elif c == "M":
            fg = Fore.BLACK
            bg = Back.CYAN
        return fg + bg

    def diff_color(self, this: str, other: str):
        "Colors for the diff view"
        if this == other:
            fg = Fore.BLACK
            bg = Back.MAGENTA
            # same
        elif this == ".":
            # freed up
            fg = Fore.GREEN
            bg = Back.GREEN
        elif this.isupper():
            # allocated Caps
            fg = Fore.YELLOW
            bg = Back.RED
        else:
            # allocated lower
            fg = Fore.WHITE
            bg = Back.RED

        return fg + bg

    def __sub__(self, other: "MemoryInfo"):
        # assume self is the newer / larger memory info
        diff = copy.deepcopy(self)
        diff.is_diff = True
        diff.used = self.used - other.used
        diff.free = self.free - other.free
        diff.one_blocks = self.one_blocks - other.one_blocks
        diff.two_blocks = self.two_blocks - other.two_blocks
        # diff.max_block_size = self.max_block_size - other.max_block_size
        # diff.max_free_size = self.max_free_size - other.max_free_size
        # diff.lines_free = self.lines_free - other.lines_free
        # diff.memory_map = self.memory_map

        # Just copy the last maps from both
        diff.memory_maps = [copy.deepcopy(self.memory_maps[-1]), copy.deepcopy(other.memory_maps[-1])]
        diff._raw_maps = [copy.deepcopy(other._raw_maps[-1]), copy.deepcopy(other._raw_maps[-1])]

        return diff

In [40]:
MemoryInfo()

In [42]:
import re
import time

mem_info = MemoryInfo()

RE_MEM_INFO = r"\*\*\* Memory info (.*) \*\*\*"
MEM_INFO_END = "-----"
# init
in_map = False
nr = 0
mem_map = []
while nr < len(log_text):
    # if the regex matches, start a new map
    if match := re.match(RE_MEM_INFO, log_text[nr]):
        mem_map = []
        in_map = True
        # get the first match
        # get the name of the map
        map_name = match[1]
    if in_map:
        if log_text[nr].startswith(MEM_INFO_END):
            # At end
            in_map = False
            if len(mem_map) > 0:
                # print("-------------------------")
                # print(mem_map)
                print(map_name)
                mem_info.append(mem_map, name= map_name)
                mem_map = []
                display(mem_info)
        else:
            mem_map.append(log_text[nr])
    nr += 1
# mem_info

_boot_fat


_boot_fat 
Memory Used: 0x6F90 of Total: 0x2EE40
Free: 0x27EB0 85.1%
MDMhhhhDhhSBMBDSDBhDh===BSB=Dh====B=BBBBBBBB=BBB=BBBBB=B=h===h== h=B=h===========h===================h=====h=================h=== 
============================================================h=== ============================================================h=hB 
SLhDB=B=Dh=SST=ShBBDBShhSBMDh==hh==h=hhhh=Sh=ShSBBBBBBBBBBBhh=== ====h========BBBhh===BhhBDBhBBBhhhBBBhh===Bhh===LhhhhShhB=h=ShLh 
=DBhSB=BBhh=Bhhhhhh===========BhSh========B=h===BB=h=h==hhh====h TLhhh=====h=======h========h==============h======Shh============ 
====h====hSLShSh===h===h=Sh..Sh===h=...h====...Sh.h==Sh===...h.. L.Sh..S.......h====..........h==h=h=h===hh=hh=h====h=h=h=....h== 
=====.....................................h.........ShShSh=..... ....Sh=........................h=======Sh=...................... 
.Sh=.....h=h=.....................................h=.h.......... .........h=.....................h=.........hh=hh.......h======h= 
==============

_onewire


_onewire 
Memory Used: 0x6B60 of Total: 0x2EE40
Free: 0x282E0 85.7%
MDMhhhhDhhSBMBDSDBhDh===BSB=Dh====B=BBBBBBBB=BBB=BBBBB=B=h===h== h=B=h===========h===================h=====h=================h=== 
============================================================h=== ============================================================h=hB 
LShDB=B=Dh=SST=ShBBDBShhSBMDh==hh==h=hhhh=Sh=ShSBBBBBBBBBBBhh=== ====h========BBBhh===BhhBDBhBBBhhhBBBhh===Bhh===LhhhhShhB=h=ShLh 
=DBhSB=BBhh=Bhhhhhh===========BhSh========B=h===SB=h=h==hhh====S .Lhhh=====h=======h========h==============h======S.h============ 
====h===.h.LShSh===Sh=.h=Sh..Sh===.....h====...Sh.h==Sh===...h.. L.Sh..Sh====..h====..........h==h=h=h===hh=hh=h====h=h=h=....h== 
=====h=======.............................h.........ShShSh=..... ....Sh=........................h=======Sh=...................... 
.Sh=.....h=h=.....................................h=.h.......... .........h=.....................h=.........hh=hh.......h======h= 
===============

_rp2


...

uzlib 
Memory Used: 0xC2C0 of Total: 0x2EE40
Free: 0x22B80 74.0%
MDMhhhhDhhSBMBDSDBhDh===BSB=Dh====B=BBBBBBBB=BBB=BBBBB=B=h===h== h=B=h===========h===================h=====h=================h=== 
============================================================h=== ============================================================h=hB 
DShDB=B=Dh=SST=ShBBDBShhSBMDh==hh==h=hhhh=Sh=ShSBBBBBBBBBBBhh=== ====h========BBBhh===BhhBDBhBBBhhhBBBhh===Bhh===LhhhSSShB=h=ShLh 
=DBhSB=BBhh=Bhhhhhh===========BhSh========B=h===SB=SBh==Lhh====M DLShh=====h=======h========h==============h======SSh============ 
====h====hSLShSh===ShSMh=ShSSSh===MDBDSh====DhSShSh==Sh===ShShh= LMShB.Sh====.Dh====.hh.Dh=.DSh==h=h=h===hh=hh=h====h=h=h=SSBDh== 
=====h=======SShBh===Sh=======hDh.SSBSh===hBBSShhSSSShShSh=h.B=B .SSDSh=h==Sh===SBBBBSSBBBBBS.B=h=======Sh=Sh========Bhh======.SS 
SSh=h===Dh=h=h=======BSSh======BSh======h========Bh=BhBBBSh===== =h======Bh=h========SSSBB=BSBhhSh=h=======Shh=hhSSh====h======h= 
==================

version


version 
Memory Used: 0xC380 of Total: 0x2EE40
Free: 0x22AC0 73.9%
MDMhhhhDhhSBMBDSDBhDh===BSB=Dh====B=BBBBBBBB=BBB=BBBBB=B=h===h== h=B=h===========h===================h=====h=================h=== 
============================================================h=== ============================================================h=hB 
DShDB=B=Dh=SST=ShBBDBShhSBMDh==hh==h=hhhh=Sh=ShSBBBBBBBBBBBhh=== ====h========BBBhh===BhhBDBhBBBhhhBBBhh===Bhh===LhhhSSShB=h=ShLh 
=DBhSB=BBhh=Bhhhhhh===========BhSh========B=h===SB=SBh==Shh====M DLLhh=====h=======h========h==============h======SSh============ 
====h====hSLShSh===ShSMh=ShSSSh===MDBDSh====DhSShSh==Sh===MDBhh= LMShBSSh===..Dh====.hh.Dh=.DSh==h=h=h===hh=hh=h====h=h=h=SSBDh== 
=====h=======SShBh===Sh=======hDh.SSBSh===hBBSShhSSSShShSh=h.B=B .SSDSh=h==Sh===SBBBBSSBBBBBS.B=h=======Sh=Sh========Bhh======.SS 
SSh=h===Dh=h=h=======BSSh======BSh======h========Bh=BhBBBSh===== =h======Bh=h========SSSBB=BSBhhSh=h=======Shh=hhSSh====h======h= 
================

zlib


zlib 
Memory Used: 0xC400 of Total: 0x2EE40
Free: 0x22A40 73.9%
MDMhhhhDhhSBMBDSDBhDh===BSB=Dh====B=BBBBBBBB=BBB=BBBBB=B=h===h== h=B=h===========h===================h=====h=================h=== 
============================================================h=== ============================================================h=hB 
DShDB=B=Dh=SST=ShBBDBShhSBMDh==hh==h=hhhh=Sh=ShSBBBBBBBBBBBhh=== ====h========BBBhh===BhhBDBhBBBhhhBBBhh===Bhh===LhhhSSShB=h=ShLh 
=DBhSB=BBhh=Bhhhhhh===========BhSh========B=h===SB=SBh==Lhh====M DLShh=====h=======h========h==============h======SSh============ 
====h====hSLShSh===ShSMh=ShSSSh===MDBDSh====DhSShSh==Sh===ShShh= LMShB.Sh===..Dh====.hh.Dh=.DSh==h=h=h===hh=hh=h====h=h=h=SSBDh== 
=====h=======SShBh===Sh=======hDh.SSBSh===hBBSShhSSSShShSh=h.B=B .SSDSh=h==Sh===SBBBBSSBBBBBS.B=h=======Sh=Sh========Bhh======.SS 
SSh=h===Dh=h=h=======BSSh======BSh======h========Bh=BhBBBSh===== =h======Bh=h========SSSBB=BSBhhSh=h=======Shh=hhSSh====h======h= 
===================

In [30]:
mem_info.memory_maps

[MemoryInfo.Info(total=192064, used=28560, free=163504, one_blocks=315, two_blocks=79, max_block_size=79, max_free_size=7888, lines_free=3, map='MDMhhhhDhhSBMBDSDBhDh===BSB=Dh====B=BBBBBBBB=BBB=BBBBB=B=h===h==h=B=h===========h===================h=====h=================h===============================================================h===============================================================h=hBSLhDB=B=Dh=SST=ShBBDBShhSBMDh==hh==h=hhhh=Sh=ShSBBBBBBBBBBBhh=======h========BBBhh===BhhBDBhBBBhhhBBBhh===Bhh===LhhhhShhB=h=ShLh=DBhSB=BBhh=Bhhhhhh===========BhSh========B=h===BB=h=h==hhh====hTLhhh=====h=======h========h==============h======Shh================h====hSLShSh===h===h=Sh..Sh===h=...h====...Sh.h==Sh===...h..L.Sh..S.......h====..........h==h=h=h===hh=hh=h====h=h=h=....h=======.....................................h.........ShShSh=.........Sh=........................h=======Sh=.......................Sh=.....h=h=.....................................h=.h...................h=............